In [5]:
# !pip install datasets
# !huggingface-cli login

In [8]:
# from datasets import load_dataset
# load_dataset("balochiml/balochi-language-data", data_dir="data", cache_dir="../data")

# Generate the processed data without English characters

In [13]:
import os

def get_txt_file_paths(directory):
    txt_file_paths = []
    for root, dirs, files in os.walk(directory):
        for file in files:
            if file.endswith(".txt"):
                file_path = os.path.join(root, file)
                txt_file_paths.append(file_path)
    return txt_file_paths

# Replace "directory_path" with the actual path of the directory you want to search
directory_path = "../data/raw_text"
txt_paths = get_txt_file_paths(directory_path)

len(txt_paths)


4294

In [17]:
import re

def clean_text(file_path):
    # Open the file and read it into memory
    with open(file_path, 'r', encoding='utf-8') as file:
        text = file.read()

    # Remove English-language characters and numbers
    text = re.sub(r'[a-zA-Z0-9]', '', text)

    # Remove any excess whitespace
    text = re.sub(r'[^\S\n]+', ' ', text)

    return text

In [18]:
for path in txt_paths:
    cleaned_text = clean_text(path)

    # write the cleaned text to a new file with an incremented filename
    # write the files all into the '../data/processed_text' directory
    with open(f'../data/processed_text/{path.split("/")[-1]}', 'w', encoding='utf-8') as file:
        file.write(cleaned_text)


In [19]:
from tokenizers import Tokenizer
from tokenizers.models import BPE

tokenizer = Tokenizer(BPE(unk_token="[UNK]"))

In [27]:
from tokenizers.trainers import BpeTrainer

# trainer = BpeTrainer(vocab_size=25000, min_frequency=2)
trainer = BpeTrainer(
    min_frequency=2,
    vocab_size=100000,
    special_tokens=["[UNK]", "[CLS]", "[SEP]", "[PAD]", "[MASK]"],
    show_progress=True,
)

In [22]:
# get a list of all the txt files in
# '/Users/strickvl/balochi/balochi-tokenizer/data/processed_text'

processed_files = get_txt_file_paths("../data/processed_text")
assert len(processed_files) == len(txt_paths)
len(processed_files)

4294

In [28]:
tokenizer.train(processed_files, trainer)

In [29]:
tokenizer.model

In [30]:
tokenizer.get_vocab_size()

100000

In [31]:
tokenizer.save("../models/balochi-tokenizer.json")